In [1]:
from nenequitia.models import AttentionalModule

model = AttentionalModule.load_from_checkpoint(
    "/home/thibault/dev/Medieval-Model/explogs/AttentionalModule/0/checkpoints/sample-epoch=21.ckpt"
)
model.eval()

AttentionalModule(
  (_emb): Sequential(
    (0): Embedding(148, 128)
    (1): Dropout(p=0.1, inplace=False)
  )
  (_rnn): LSTM(128, 256, batch_first=True, bidirectional=True)
  (_rnn_dropout): Dropout(p=0.1, inplace=False)
  (_rnn_dense): Linear(in_features=512, out_features=512, bias=False)
  (_lin): Sequential(
    (0): Dropout(p=0.1, inplace=False)
    (1): Linear(in_features=512, out_features=4, bias=True)
  )
)

In [2]:
from pandas import read_hdf

df = read_hdf("texts.hdf5", key="df", index_col=0)
df = df[df.manuscript == "SBB_PK_Hdschr25"]
df["bin"] = ""
df.loc[df.CER < 10, "bin"] = "Good"
df.loc[df.CER.between(10, 20, inclusive="left"), "bin"] = "Acceptable"
df.loc[df.CER.between(20, 50, inclusive="left"), "bin"] = "Bad"
df.loc[df.CER >= 50, "bin"] = "Very bad"
df.tail()

transcription                           model  \
71436    nisam a labus iquis:ta  data-cremma-medieval_0.mlmodel   
166                           m         data-lat_only_3.mlmodel   
65002  uisti.eEt qloriamiu oims              data-bad_1.mlmodel   
22371  bredicaut tuinairegentẽ  data-cremma-medieval_2.mlmodel   
196                     ⁊ p p a         data-lat_only_3.mlmodel   

            manuscript  page_id  line_id        CER lang       bin  
71436  SBB_PK_Hdschr25        7        8  37.037036  lat       Bad  
166    SBB_PK_Hdschr25       12        2  71.428573  lat  Very bad  
65002  SBB_PK_Hdschr25       16        6  40.740740  lat       Bad  
22371  SBB_PK_Hdschr25       14        6  23.076923  lat       Bad  
196    SBB_PK_Hdschr25       14        5  85.714287  lat  Very bad

In [13]:
from nenequitia.metrics import computer_cer
from collections import Counter
from unicodedata import combining, normalize
from IPython.core.display import display, HTML

pages = []
lines = []
labels = ['Good', 'Acceptable', 'Bad', 'Very bad']
for (local_model, m, p), group in df.groupby(["model", "manuscript", "page_id"]):
    page = group.sort_values("line_id")
    gt = df[(df.model == "GT") & (df.manuscript == m) & (df.page_id == p)]
    page = "".join(group.transcription.tolist())
    gt = "".join(gt.transcription.tolist())
    cer = min(computer_cer(page, gt)*100, 100)
    print(f"{p} for model `{local_model}` CER is {cer}%")
    preds, attention = model(*model.encoder.pad_pred([
        model.encoder.encode_string(string, lang="lat")
        for string in group.transcription.tolist()
    ]))
    preds = preds.argmax(dim=-1).tolist()
    #print(model.encoder.ys)
    pages.append({"cer": cer, "counter": Counter([model.encoder.ys[pred] for pred in preds])})
    for line_attention, line, line_pred in zip(attention.tolist(), group.transcription.tolist(), preds):
        max_attention = max(line_attention)
        colors = [int(255*(att/max_attention)) for att in line_attention]
        if True:
            display(HTML(
                f"<b>Prediction: {model.encoder.ys[line_pred]}</b> " + "".join([
                   f'<span style="color:rgb({color}, 0, 0);" title="{char_att:.2f}">{char}</span>'
                    for color, char_att, char in zip(
                        colors,
                        line_attention,
                        (
                            ["[BOS] ", "[LANG] "] + 
                            [(normalize("NFC", "◌"+char) if combining(char) != 0 else char)for char in line]+
                            [" [EOS] "]
                        )
                    )
                ])
            ))


            

0 for model `GT` CER is 0.0%


/tmp/ipykernel_49772/247148208.py:4: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display
  from IPython.core.display import display, HTML


1 for model `GT` CER is 0.0%


2 for model `GT` CER is 0.0%


3 for model `GT` CER is 0.0%


...

13 for model `data-manumffrench2.mlmodel` CER is 67.70186424255371%


14 for model `data-manumffrench2.mlmodel` CER is 77.2357702255249%


15 for model `data-manumffrench2.mlmodel` CER is 73.27044010162354%


16 for model `data-manumffrench2.mlmodel` CER is 69.35483813285828%


[('Very bad', 10)]


In [ ]:

print(pages[-1]["counter"].most_common(1))